In [3]:
# 加载数据
import pandas as pd
cleaned_data = pd.read_csv('conc_unconfine.csv')
cleaned_data

row  col       x       y    top          K model_name  nlay  \
0          0    6   650.0    50.0  100.0  34.560001     Sub_80     1   
1          0    7   750.0    50.0  100.0  34.560001     Sub_80     1   
2          0    8   850.0    50.0  100.0  34.560001     Sub_80     1   
3          0    9   950.0    50.0  100.0  34.560001     Sub_80     1   
4          0   10  1050.0    50.0  100.0  34.560001     Sub_80     1   
...      ...  ...     ...     ...    ...        ...        ...   ...   
3551995   28   43  4350.0  2850.0  100.0   1.000000     Sub_17     1   
3551996   29   38  3850.0  2950.0  100.0  25.920000     Sub_17     1   
3551997   29   39  3950.0  2950.0  100.0  25.920000     Sub_17     1   
3551998   29   40  4050.0  2950.0  100.0  60.480000     Sub_17     1   
3551999   29   41  4150.0  2950.0  100.0  60.480000     Sub_17     1   

         time_step  layer  ...        head  concentration  chd_mask  recharge  \
0                0      0  ...  100.000000       0.000002       1.0  0.013073   
1                0      0  ...  100.948244       0.000007       0.0  0.013073   
2                0      0  ...  101.767935       0.000019       0.0  0.013073   
3                0      0  ...  102.449170       0.000043       0.0  0.013073   
4                0      0  ...  102.999759       0.000093       0.0  0.013073   
...            ...    ...  ...         ...            ...       ...       ...   
3551995         39      0  ...   80.000000       0.000000       0.0  0.000000   
3551996         39      0  ...   87.717118       0.328380       0.0  0.018023   
3551997         39      0  ...   85.811535       0.189496       0.0  0.018023   
3551998         39      0  ...   83.088839       0.072939       0.0  0.022320   
3551999         39      0  ...   80.000000       0.008353       0.0  0.022320   

               ET  river_stage  river_cond  river_rbot  well_rate  well_mask  
0        0.002428          0.0         0.0         0.0        0.0        0.0  
1        0.002428          0.0         0.0         0.0        0.0        0.0  
2        0.002428          0.0         0.0         0.0        0.0        0.0  
3        0.002428          0.0         0.0         0.0        0.0        0.0  
4        0.002428          0.0         0.0         0.0        0.0        0.0  
...           ...          ...         ...         ...        ...        ...  
3551995  0.000000          0.0         0.0         0.0        0.0        0.0  
3551996  0.003358          0.0         0.0         0.0        0.0        0.0  
3551997  0.003358          0.0         0.0         0.0        0.0        0.0  
3551998  0.004158          0.0         0.0         0.0        0.0        0.0  
3551999  0.004158          0.0         0.0         0.0        0.0        0.0  

[3552000 rows x 21 columns]

In [26]:
import pandas as pd
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch_geometric.nn import MessagePassing
from torch_geometric.loader import DataLoader
from torch_geometric.data import Data
from torch_geometric.utils import add_self_loops
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
import numpy as np
import os
from torch.cuda.amp import GradScaler, autocast

# 设备配置
device = torch.device('cuda:1' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")

# 自定义数据集类
class HydroDataset(torch.utils.data.Dataset):
    def __init__(self, graphs):
        self.graphs = graphs
        
    def __len__(self):
        return len(self.graphs)
    
    def __getitem__(self, idx):
        return self.graphs[idx]

class STConv(MessagePassing):
    def __init__(self, spatial_dim):
        super().__init__(aggr='mean')
        self.msg_net = nn.Sequential(
            nn.Linear(2 * spatial_dim + 3, spatial_dim),
            nn.ReLU(),
            nn.LayerNorm(spatial_dim)
        )
        self.gate_net = nn.Sequential(
            nn.Linear(3 * spatial_dim, spatial_dim),
            nn.Sigmoid()
        )

    def forward(self, x, edge_index, edge_attr):
        out = self.propagate(edge_index, x=x, edge_attr=edge_attr)
        gate = self.gate_net(torch.cat([x, out, x - out], dim=-1))
        return x + gate * out

    def message(self, x_i, x_j, edge_attr):
        edge_attr = edge_attr.to(x_i.dtype)
        return self.msg_net(torch.cat([x_i, x_j, edge_attr], dim=-1))

class BoundaryProcessor(nn.Module):
    def __init__(self, dim):
        super().__init__()
        self.boundary_net = nn.Sequential(
            nn.Linear(dim + 1, dim),
            nn.ReLU()
        )
        self.river_net = nn.Sequential(
            nn.Linear(dim + 2, dim),
            nn.ReLU()
        )
        self.well_net = nn.Linear(dim + 1, dim)
        self.gate = nn.Sequential(
            nn.Linear(2 * dim, dim),
            nn.Sigmoid()
        )

    def forward(self, x, bc_mask):
        boundary_feat = self.boundary_net(
            torch.cat([x, bc_mask[:, 0:1]], dim=-1)
        ) * bc_mask[:, 0:1]
        river_feat = self.river_net(
            torch.cat([x, bc_mask[:, 1:3]], dim=-1)
        ) * bc_mask[:, 1:2]
        well_feat = self.well_net(
            torch.cat([x, bc_mask[:, 3:4]], dim=-1)
        ) * bc_mask[:, 4:5]
        combined = boundary_feat + river_feat + well_feat
        gate = self.gate(torch.cat([x, combined], dim=-1))
        return x * (1 - gate) + combined * gate

class HeadGNN(nn.Module):
    def __init__(self, node_features=13, max_time_steps=40, spatial_dim=64, temporal_dim=64, output_dim=1):
        super().__init__()
        self.time_embed = nn.Embedding(max_time_steps + 1, temporal_dim)
        self.node_enc = nn.Sequential(
            nn.Linear(node_features + temporal_dim, spatial_dim),
            nn.ReLU(),
            nn.LayerNorm(spatial_dim)
        )
        self.conv_layers = nn.ModuleList([STConv(spatial_dim) for _ in range(4)])
        self.bc_processor = BoundaryProcessor(spatial_dim)
        self.decoder = nn.Sequential(
            nn.Linear(spatial_dim, 64),
            nn.ReLU(),
            nn.Dropout(0.1),
            nn.Linear(64, output_dim),
            nn.Softplus()
        )

    def forward(self, data):
        x, edge_index, edge_attr = data.x, data.edge_index, data.edge_attr.to(torch.float32)
        time_emb = self.time_embed(data.time_step)
        node_feat = torch.cat([x[:, :13], time_emb], dim=-1)  # 只使用前 13 个特征
        h = self.node_enc(node_feat)
        for conv in self.conv_layers:
            h = conv(h, edge_index, edge_attr)
        h = self.bc_processor(h, data.bc_mask)
        return self.decoder(h)

class ConcGNN(nn.Module):
    def __init__(self, node_features=15, max_time_steps=40, spatial_dim=64, temporal_dim=64, output_dim=1):
        super().__init__()
        self.time_embed = nn.Embedding(max_time_steps + 1, temporal_dim)
        self.node_enc = nn.Sequential(
            nn.Linear(node_features + temporal_dim, spatial_dim),
            nn.ReLU(),
            nn.Dropout(0.1),
            nn.LayerNorm(spatial_dim)
        )
        self.conv_layers = nn.ModuleList([STConv(spatial_dim) for _ in range(4)])
        self.bc_processor = BoundaryProcessor(spatial_dim)
        self.decoder = nn.Sequential(
            nn.Linear(spatial_dim, 64),
            nn.ReLU(),
            nn.Linear(64, output_dim),
            nn.Softplus()
        )

    def forward(self, data):
        x, edge_index, edge_attr = data.x, data.edge_index, data.edge_attr.to(torch.float32)
        time_emb = self.time_embed(data.time_step)
        node_feat = torch.cat([x, time_emb], dim=-1)
        h = self.node_enc(node_feat)
        for conv in self.conv_layers:
            h = conv(h, edge_index, edge_attr)
        h = self.bc_processor(h, data.bc_mask)
        return self.decoder(h)


class PhysicsInformedLoss(nn.Module):
    def __init__(self, alpha=0.5):
        super().__init__()
        self.alpha = alpha

    def forward(self, pred, data):
        mse_loss = F.mse_loss(pred, data.head_y.unsqueeze(1))  # 归一化水位损失
        time_steps = data.time_step.unique(sorted=True)
        flux_loss = 0
        for t in time_steps[:-1]:
            mask_t = (data.time_step == t)
            mask_next = (data.time_step == t + 1)
            flux_diff = torch.mean((pred[mask_next] - pred[mask_t]) ** 2)
            flux_loss += flux_diff
        flux_loss /= len(time_steps) - 1 if len(time_steps) > 1 else 1
        bc_mask = data.bc_mask[:, 0] > 0
        bc_loss = F.l1_loss(pred[bc_mask], data.head_y[bc_mask].unsqueeze(1)) if bc_mask.sum() > 0 else torch.tensor(0.0, device=pred.device)
        well_mask = data.bc_mask[:, 4] > 0
        well_loss = F.l1_loss(pred[well_mask], data.head_y[well_mask].unsqueeze(1)) if well_mask.sum() > 0 else torch.tensor(0.0, device=pred.device)
        total_loss = (1 - self.alpha) * mse_loss + self.alpha * (0.2 * flux_loss + 0.7 * bc_loss + 0.1 * well_loss)
        return total_loss, (mse_loss.item(), flux_loss.item(), bc_loss.item(), well_loss.item())

class ConcLoss(nn.Module):
    def __init__(self):
        super().__init__()

    def forward(self, pred, data):
        # 直接在非归一化空间计算浓度损失
        mse_loss = F.mse_loss((pred), (data.y.unsqueeze(1)))  # pred 和 y 都是非归一化的
        # mse_loss = F.mse_loss(torch.log1p(pred), torch.log1p(data.y.unsqueeze(1)))  # pred 和 y 都是非归一化的
        return mse_loss, (mse_loss.item(),)

def generate_spatial_edges(model_df):
    spatial_edges = []
    time_steps = model_df['time_step'].unique()
    for t in time_steps:
        time_df = model_df[model_df['time_step'] == t]
        coord_to_idx = {(r, c): idx for idx, r, c in zip(time_df['local_index'], time_df['row'], time_df['col'])}
        for idx, row, col in zip(time_df['local_index'], time_df['row'], time_df['col']):
            right_coord = (row, col + 1)
            if right_coord in coord_to_idx:
                spatial_edges.append([idx, coord_to_idx[right_coord]])
            upper_coord = (row + 1, col)
            if upper_coord in coord_to_idx:
                spatial_edges.append([idx, coord_to_idx[upper_coord]])
    return np.array(spatial_edges), np.full((len(spatial_edges), 3), [1.0, 0, 0], dtype=np.float32)

def generate_temporal_edges(model_df):
    temporal_edges = []
    groups = model_df.groupby(['row', 'col'], sort=False)
    for (row, col), group in groups:
        time_series = group.sort_values('time_step')
        for i in range(len(time_series) - 1):
            global_src = time_series['local_index'].iloc[i]
            global_dst = time_series['local_index'].iloc[i + 1]
            temporal_edges.append([global_src, global_dst])
    return np.array(temporal_edges), np.full((len(temporal_edges), 3), [0.0, 1.0, 0], dtype=np.float32)

def build_bc_mask(model_df):
    bc_mask = np.zeros((len(model_df), 5), dtype=np.float32)
    bc_mask[:, 0] = model_df['chd_mask'].values.astype(np.float32)
    bc_mask[:, 1] = (model_df['river_cond'] > 0).astype(np.float32)
    bc_mask[:, 2] = model_df['river_stage'].values.astype(np.float32)
    bc_mask[:, 3] = model_df['well_rate'].values.astype(np.float32)
    bc_mask[:, 4] = model_df['well_mask'].values.astype(np.float32)
    return bc_mask

def prepare_data(data, batch_size=4):
    print('正在处理')
    all_graphs = build_spatiotemporal_graph(data)
    print('处理完成')
    train_val_graphs, test_graphs = train_test_split(
        all_graphs, test_size=0.15, random_state=42
    )
    train_graphs, val_graphs = train_test_split(
        train_val_graphs, test_size=0.1765, random_state=42
    )
    train_dataset = HydroDataset(train_graphs)
    val_dataset = HydroDataset(val_graphs)
    test_dataset = HydroDataset(test_graphs)
    train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_dataset, batch_size=batch_size)
    test_loader = DataLoader(test_dataset, batch_size=batch_size)
    return train_loader, val_loader, test_loader


Using device: cuda:1


In [46]:
import numpy as np
import torch
from torch_geometric.data import Data
from sklearn.preprocessing import MinMaxScaler, StandardScaler, RobustScaler

def build_spatiotemporal_graph(df):
    print(f"\n▶ Started building spatiotemporal graphs")
    print(f"▷ Total models to process: {len(df['model_name'].unique())}")
    graphs = []
    
    # 转换数据类型
    df = df.astype({
        'x': np.float32, 'y': np.float32, 'top': np.float32, 
        'bottom': np.float32, 'K': np.float32, 'recharge': np.float32,
        'ET': np.float32, 'river_stage': np.float32, 'river_cond': np.float32,
        'river_rbot': np.float32, 'well_rate': np.float32, 'well_mask': np.uint8,
        'chd_mask': np.uint8, 'head': np.float32, 'concentration': np.float32
    })
    time_min = df['time_step'].min()
    df['time_step'] = df['time_step'] - time_min
    
    model_groups = list(df.groupby('model_name', sort=False))
    total_models = len(model_groups)
    
    for model_idx, (model_name, model_df) in enumerate(model_groups, 1):
        model_df = model_df.reset_index(drop=True).copy()
        model_df['local_index'] = model_df.index
        print(f"\n▣ Processing model {model_idx}/{total_models}: {model_name}")
        
        model_df = model_df.sort_values(['row', 'col', 'time_step'])
        
        # 节点特征
        node_feats = model_df[[
            'x', 'y', 'top', 'bottom', 'K', 'recharge', 'ET',
            'river_stage', 'river_cond', 'river_rbot', 'well_rate', 'well_mask'
        ]].values.astype(np.float32)
        prev_head = np.zeros(len(model_df), dtype=np.float32)
        prev_conc = np.zeros(len(model_df), dtype=np.float32)
        groups = model_df.groupby(['row', 'col'], sort=False)
        for (row, col), group in groups:
            time_series = group.sort_values('time_step')
            prev_head[time_series.index] = np.roll(time_series['head'].values, 1)
            prev_conc[time_series.index] = np.roll(time_series['concentration'].values, 1)
            first_idx = time_series.index[0]
            prev_head[first_idx] = 0.0
            prev_conc[first_idx] = 0.0
        node_feats = np.concatenate([node_feats, prev_head[:, None], prev_conc[:, None]], axis=1)
        
        # 处理节点特征中的 NaN 和 Inf
        if np.any(np.isnan(node_feats)) or np.any(np.isinf(node_feats)):
            print(f"Warning: node_feats contains NaN or Inf for model {model_name}")
            node_feats = np.nan_to_num(node_feats, nan=0.0, posinf=1e6, neginf=-1e6)
        
        # 节点特征标准化 (MinMaxScaler)
        feature_scaler = MinMaxScaler()
        node_feats = feature_scaler.fit_transform(node_feats)
        
        # 浓度数据标准化 (RobustScaler)
        # conc = model_df['concentration'].values.astype(np.float32)
        # if np.any(np.isnan(conc)) or np.any(np.isinf(conc)):
        #     print(f"Warning: concentration contains NaN or Inf for model {model_name}")
        #     conc = np.nan_to_num(conc, nan=0.0, posinf=1e6, neginf=-1e6)
        # conc_scaler = RobustScaler()
        # conc_normalized = conc_scaler.fit_transform(conc.reshape(-1, 1)).flatten()
        
        # # 水头数据标准化 (StandardScaler)
        # head = model_df['head'].values.astype(np.float32)
        # if np.any(np.isnan(head)) or np.any(np.isinf(head)):
        #     print(f"Warning: head contains NaN or Inf for model {model_name}")
        #     head = np.nan_to_num(head, nan=0.0, posinf=1e6, neginf=-1e6)
        # head_scaler = StandardScaler()
        # head_normalized = head_scaler.fit_transform(head.reshape(-1, 1)).flatten()
        # 输出直接使用未归一化的真实物理值
        conc = model_df['concentration'].values.astype(np.float32)
        head = model_df['head'].values.astype(np.float32)
        # 边和边属性
        spatial_edges, spatial_attrs = generate_spatial_edges(model_df)
        temporal_edges, temporal_attrs = generate_temporal_edges(model_df)
        edges = np.concatenate([spatial_edges, temporal_edges], axis=0)
        edge_attr = np.concatenate([spatial_attrs, temporal_attrs], axis=0)
        
        # 边界条件掩码
        bc_mask = build_bc_mask(model_df)
        
        # 创建图数据对象
        graph = Data(
            x=torch.from_numpy(node_feats),
            edge_index=torch.tensor(edges.T, dtype=torch.long),
            edge_attr=torch.from_numpy(edge_attr),
            y=torch.from_numpy(conc),
            head_y=torch.from_numpy(head),
            bc_mask=torch.from_numpy(bc_mask),
            time_step=torch.from_numpy(model_df['time_step'].values).long(),
            time_steps=model_df['time_step'].nunique(),
            # head_scaler=head_scaler,  # 存储为单元素列表以兼容后续代码
            # conc_scaler=conc_scaler,  # 存储为单元素列表以兼容后续代码
            model_name=str(model_name),
            row=torch.from_numpy(model_df['row'].values).long(),
            col=torch.from_numpy(model_df['col'].values).long(),
        )
        graphs.append(graph)
    
    print(f"\n✅ All models processed! Total graphs created: {len(graphs):,}")
    return graphs

In [47]:
train_loader, val_loader, test_loader = prepare_data(cleaned_data)

正在处理

▶ Started building spatiotemporal graphs
▷ Total models to process: 100

▣ Processing model 1/100: Sub_80

▣ Processing model 2/100: Sub_37

▣ Processing model 3/100: Sub_61

▣ Processing model 4/100: Sub_83

▣ Processing model 5/100: Sub_85

▣ Processing model 6/100: Sub_42

▣ Processing model 7/100: Sub_12

▣ Processing model 8/100: Sub_66

▣ Processing model 9/100: Sub_72

▣ Processing model 10/100: Sub_82

▣ Processing model 11/100: Sub_79

▣ Processing model 12/100: Sub_5

▣ Processing model 13/100: Sub_30

▣ Processing model 14/100: Sub_33

▣ Processing model 15/100: Sub_58

▣ Processing model 16/100: Sub_44

▣ Processing model 17/100: Sub_27

▣ Processing model 18/100: Sub_73

▣ Processing model 19/100: Sub_10

▣ Processing model 20/100: Sub_1

▣ Processing model 21/100: Sub_35

▣ Processing model 22/100: Sub_62

▣ Processing model 23/100: Sub_23

▣ Processing model 24/100: Sub_68

▣ Processing model 25/100: Sub_78

▣ Processing model 26/100: Sub_6

▣ Processing model 27/1

/opt/conda/lib/python3.11/site-packages/torch_geometric/deprecation.py:26: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


In [52]:
import pandas as pd
import torch
import torch.nn.functional as F
import numpy as np
from torch_geometric.data import Data, DataLoader
import os
from torch.cuda.amp import autocast, GradScaler
import matplotlib.pyplot as plt
from torch.optim.lr_scheduler import CosineAnnealingLR
from sklearn.preprocessing import StandardScaler, RobustScaler
from sklearn.metrics import r2_score as sklearn_r2_score

# Training configuration
config = {
    'head_input_dim': 13,
    'conc_input_dim': 15,
    'hidden_dim': 64,
    'num_epochs': 200,
    'lr': 5e-3,
    'weight_decay': 1e-5,
    'patience': 20,
    'save_path': './saved_models'
}

device = torch.device('cuda:1' if torch.cuda.is_available() else 'cpu')
print(f"Selected device: {device}")

def r2_score(y_true, y_pred):
    """
    使用 sklearn.metrics.r2_score 计算 R² 分数，包含 NaN 和 Inf 检查。
    
    参数:
        y_true: 真实值张量
        y_pred: 预测值张量
    
    返回:
        R² 分数，若输入无效则返回 np.nan
    """
    try:
        y_true = y_true.detach().cpu().numpy().flatten()
        y_pred = y_pred.detach().cpu().numpy().flatten()
        
        # 检查输入长度
        if len(y_true) != len(y_pred):
            print(f"Error: y_true and y_pred length mismatch: {len(y_true)} vs {len(y_pred)}")
            return np.nan
        
        # 检查 NaN 或 Inf
        if np.any(np.isnan(y_true)) or np.any(np.isinf(y_true)):
            print("Error: y_true contains NaN or Inf")
            return np.nan
        if np.any(np.isnan(y_pred)) or np.any(np.isinf(y_pred)):
            print("Error: y_pred contains NaN or Inf")
            return np.nan
        
        # 计算 sklearn 的 R² 分数
        r2 = sklearn_r2_score(y_true, y_pred)
        
        # 调试信息：打印 R² 和数据统计
        print(f"R²: {r2:.6f}")
        print(f"y_true mean: {np.mean(y_true):.6f}, variance: {np.var(y_true):.6f}")
        print(f"y_true range: min={np.min(y_true):.6f}, max={np.max(y_true):.6f}")
        print(f"y_pred range: min={np.min(y_pred):.6f}, max={np.max(y_pred):.6f}")
        
        # 检查 R² 异常
        if r2 > 1 or r2 < -1:
            print(f"Warning: Abnormal R² value: {r2}")
            print(f"y_true sample: {y_true[:5]}")
            print(f"y_pred sample: {y_pred[:5]}")
        
        return r2
    
    except Exception as e:
        print(f"Error in r2_score: {e}")
        return np.nan



def train():
    try:
        torch.cuda.empty_cache()
        print("CUDA缓存已成功清除")
    except RuntimeError as e:
        print(f"无法清除CUDA缓存: {e}")
        return None, None

    grad_scaler = GradScaler()
    head_model = HeadGNN(
        node_features=config['head_input_dim'],
        spatial_dim=config['hidden_dim'],
        temporal_dim=config['hidden_dim']
    ).to(device)
    conc_model = ConcGNN(
        node_features=config['conc_input_dim'],
        spatial_dim=config['hidden_dim'],
        temporal_dim=config['hidden_dim']
    ).to(device)
    criterion_head = PhysicsInformedLoss()
    criterion_conc = ConcLoss()
    optimizer = torch.optim.AdamW(
        list(head_model.parameters()) + list(conc_model.parameters()),
        lr=config['lr'],
        weight_decay=config['weight_decay']
    )
    scheduler = CosineAnnealingLR(optimizer, T_max=config['num_epochs'] * 2, eta_min=1e-5)
    best_val_loss = float('inf')
    early_stop_counter = 0
    accum_steps = 4
    losses = {'train': [], 'val': []}

    for epoch in range(config['num_epochs']):
        head_model.train()
        conc_model.train()
        total_train_loss = 0
        train_batches = 0

        optimizer.zero_grad()
        for batch_idx, batch in enumerate(train_loader):
            batch = batch.to(device)
            if batch.x.device != device or batch.batch.device != device:
                print(f"批次 {batch_idx} 设备不匹配: x={batch.x.device}, batch={batch.batch.device}")
                continue

            with torch.amp.autocast("cuda", enabled=True):
                pred_head = head_model(batch)
                
                if torch.any(torch.isnan(pred_head)) or torch.any(torch.isinf(pred_head)):
                    print(f"批次 {batch_idx}: pred_head 包含 NaN 或 Inf")
                    continue
                if torch.any(torch.isnan(batch.head_y)) or torch.any(torch.isinf(batch.head_y)):
                    print(f"批次 {batch_idx}: head_y 包含 NaN 或 Inf")
                    continue

                batch_conc = batch.clone()
                pred_head_2d = pred_head.view(-1, 1) if pred_head.dim() > 2 else pred_head
                batch_conc.x = torch.cat([batch.x, pred_head_2d], dim=1)
                pred_conc = conc_model(batch_conc)

                if torch.any(torch.isnan(pred_conc)) or torch.any(torch.isinf(pred_conc)):
                    print(f"批次 {batch_idx}: pred_conc 包含 NaN 或 Inf")
                    continue
                if torch.any(torch.isnan(batch.y)) or torch.any(torch.isinf(batch.y)):
                    print(f"批次 {batch_idx}: y 包含 NaN 或 Inf")
                    continue

                head_loss, _ = criterion_head(pred_head, batch)
                conc_loss, _ = criterion_conc(pred_conc, batch)
                # loss = (0.5 * head_loss + 0.5 * conc_loss) / accum_steps
                w_head = 1.0 / (head_loss.item() + 1e-8)
                w_conc = 1.0 / (conc_loss.item() + 1e-8)
                w_sum = w_head + w_conc
                w_head /= w_sum
                w_conc /= w_sum
                loss = w_head * head_loss + w_conc * conc_loss

            grad_scaler.scale(loss).backward()
            if (batch_idx + 1) % accum_steps == 0:
                torch.nn.utils.clip_grad_norm_(list(head_model.parameters()) + list(conc_model.parameters()), max_norm=1.0)
                grad_scaler.step(optimizer)
                grad_scaler.update()
                optimizer.zero_grad()
            total_train_loss +=loss
            # total_train_loss += (head_loss.item() + conc_loss.item()) / 2
            train_batches += 1

        head_model.eval()
        conc_model.eval()
        total_val_loss = 0
        val_batches = 0

        with torch.no_grad():
            for batch in val_loader:
                batch = batch.to(device)
                with torch.amp.autocast("cuda", enabled=True):
                    pred_head = head_model(batch)
                    
                    if torch.any(torch.isnan(pred_head)) or torch.any(torch.isinf(pred_head)):
                        print(f"验证批次: pred_head 包含 NaN 或 Inf")
                        continue
                    if torch.any(torch.isnan(batch.head_y)) or torch.any(torch.isinf(batch.head_y)):
                        print(f"验证批次: head_y 包含 NaN 或 Inf")
                        continue

                    batch_conc = batch.clone()
                    pred_head_2d = pred_head.view(-1, 1) if pred_head.dim() > 2 else pred_head
                    batch_conc.x = torch.cat([batch.x, pred_head_2d], dim=1)
                    pred_conc = conc_model(batch_conc)

                    if torch.any(torch.isnan(pred_conc)) or torch.any(torch.isinf(pred_conc)):
                        print(f"验证批次: pred_conc 包含 NaN 或 Inf")
                        continue
                    if torch.any(torch.isnan(batch.y)) or torch.any(torch.isinf(batch.y)):
                        print(f"验证批次: y 包含 NaN 或 Inf")
                        continue
                    
                    head_loss, _ = criterion_head(pred_head, batch)
                    conc_loss, _ = criterion_conc(pred_conc, batch)
                    w_head = 1.0 / (head_loss.item() + 1e-8)
                    w_conc = 1.0 / (conc_loss.item() + 1e-8)
                    w_sum = w_head + w_conc
                    w_head /= w_sum
                    w_conc /= w_sum
                    loss = w_head * head_loss + w_conc * conc_loss
                    # loss = (head_loss.item() + conc_loss.item()) / 2
                    # loss = head_loss.item()

                total_val_loss += loss
                val_batches += 1

        if train_batches == 0 or val_batches == 0:
            print(f"Epoch {epoch+1}: 无有效批次 (train_batches={train_batches}, val_batches={val_batches})")
            continue

        # avg_train_loss = total_train_loss / train_batches
        # avg_val_loss = total_val_loss / val_batches
        avg_train_loss = (total_train_loss / train_batches).item()
        avg_val_loss = (total_val_loss / val_batches).item()
        losses['train'].append(avg_train_loss)
        losses['val'].append(avg_val_loss)

        print(f"Epoch {epoch+1:03d} | 训练损失: {avg_train_loss:.4f} | 验证损失: {avg_val_loss:.4f}")

        scheduler.step()
        if avg_val_loss < best_val_loss:
            best_val_loss = avg_val_loss
            early_stop_counter = 0
            os.makedirs(config['save_path'], exist_ok=True)
            torch.save({
                'head_model': head_model.state_dict(),
                'conc_model': conc_model.state_dict(),
            }, os.path.join(config['save_path'], 'best_model.pth'))
        else:
            early_stop_counter += 1

        if torch.cuda.is_available():
            torch.cuda.empty_cache()

        if early_stop_counter >= config['patience']:
            print("早停触发！")
            break

    # 保存训练和验证损失
    losses_df = pd.DataFrame({
        'epoch': range(1, len(losses['train']) + 1),
        'train_loss': losses['train'],
        'val_loss': losses['val']
    })
    losses_df.to_csv(os.path.join(config['save_path'], 'losses.csv'), index=False)
    print(f"训练和验证损失已保存至 {os.path.join(config['save_path'], 'losses.csv')}")

    return None, None
def evaluate():
    head_model = HeadGNN(
        node_features=config['head_input_dim'],
        spatial_dim=config['hidden_dim'],
        temporal_dim=config['hidden_dim']
    ).to(device)
    conc_model = ConcGNN(
        node_features=config['conc_input_dim'],
        spatial_dim=config['hidden_dim'],
        temporal_dim=config['hidden_dim']
    ).to(device)
    checkpoint = torch.load(os.path.join(config['save_path'], 'best_model.pth'))
    head_model.load_state_dict(checkpoint['head_model'])
    conc_model.load_state_dict(checkpoint['conc_model'])
    
    head_model.eval()
    conc_model.eval()
    test_loss = 0
    metrics = {'mse_conc': 0, 'mae_conc': 0, 'mse_head': 0, 'r2_conc': 0, 'r2_head': 0}
    predictions = []

    with torch.no_grad():
        for batch in test_loader:
            batch = batch.to(device)
            with torch.amp.autocast("cuda", enabled=True):
                pred_head = head_model(batch)
                batch_conc = batch.clone()
                pred_head_2d = pred_head.view(-1, 1) if pred_head.dim() > 2 else pred_head
                batch_conc.x = torch.cat([batch.x, pred_head_2d], dim=1)
                pred_conc = conc_model(batch_conc)

                head_loss = F.mse_loss(pred_head, batch.head_y.unsqueeze(1))
                conc_loss = F.mse_loss(pred_conc, batch.y.unsqueeze(1))
                w_head = 1.0 / (head_loss.item() + 1e-8)
                w_conc = 1.0 / (conc_loss.item() + 1e-8)
                w_sum = w_head + w_conc
                w_head /= w_sum
                w_conc /= w_sum
                loss = w_head * head_loss + w_conc * conc_loss
            # test_loss += (head_loss.item() + conc_loss.item()) / 2
            test_loss += loss
            mse_conc = F.mse_loss(pred_conc, batch.y.unsqueeze(1)).item()
            mae_conc = F.l1_loss(pred_conc, batch.y.unsqueeze(1)).item()
            mse_head = F.mse_loss(pred_head, batch.head_y.unsqueeze(1)).item()
            r2_conc = r2_score(batch.y.unsqueeze(1), pred_conc)
            r2_head = r2_score(batch.head_y.unsqueeze(1), pred_head)

            metrics['mse_conc'] += mse_conc
            metrics['mae_conc'] += mae_conc
            metrics['mse_head'] += mse_head
            metrics['r2_conc'] += r2_conc
            metrics['r2_head'] += r2_head

            predictions.append({
                'row': batch.row.cpu().numpy(),
                'col': batch.col.cpu().numpy(),
                'time_step': batch.time_step.cpu().numpy(),
                'pred_conc': pred_conc.cpu().numpy().flatten(),
                'true_conc': batch.y.cpu().numpy().flatten(),
                'pred_head': pred_head.cpu().numpy().flatten(),
                'true_head': batch.head_y.cpu().numpy().flatten()
            })

    num_batches = len(test_loader)
    metrics = {k: v / num_batches for k, v in metrics.items()}

    print("\n测试结果:")
    print(f"总损失: {test_loss/num_batches:.4f}")
    print(f"浓度 MSE: {metrics['mse_conc']:.4f}")
    print(f"浓度 MAE: {metrics['mae_conc']:.4f}")
    print(f"水头 MSE: {metrics['mse_head']:.4f}")
    print(f"浓度 R²: {metrics['r2_conc']:.4f}")
    print(f"水头 R²: {metrics['r2_head']:.4f}")

    predictions_df = pd.DataFrame()
    for pred in predictions:
        df = pd.DataFrame(pred)
        predictions_df = pd.concat([predictions_df, df], ignore_index=True)
    predictions_df.to_csv(os.path.join(config['save_path'], 'test_predictions.csv'), index=False)

    return metrics, predictions


Selected device: cuda:1


In [53]:
train()
evaluate()

CUDA缓存已成功清除


/tmp/ipykernel_144/4010432150.py:87: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  grad_scaler = GradScaler()


Epoch 001 | 训练损失: 0.2496 | 验证损失: 0.1710
Epoch 002 | 训练损失: 0.1546 | 验证损失: 0.1333
Epoch 003 | 训练损失: 0.1288 | 验证损失: 0.1256
Epoch 004 | 训练损失: 0.1259 | 验证损失: 0.1219
Epoch 005 | 训练损失: 0.1253 | 验证损失: 0.1223
Epoch 006 | 训练损失: 0.1258 | 验证损失: 0.1216
Epoch 007 | 训练损失: 0.1244 | 验证损失: 0.1209
Epoch 008 | 训练损失: 0.1259 | 验证损失: 0.1225
Epoch 009 | 训练损失: 0.1240 | 验证损失: 0.1188
Epoch 010 | 训练损失: 0.1240 | 验证损失: 0.1179
Epoch 011 | 训练损失: 0.1221 | 验证损失: 0.1172
Epoch 012 | 训练损失: 0.1209 | 验证损失: 0.1176
Epoch 013 | 训练损失: 0.1211 | 验证损失: 0.1173
Epoch 014 | 训练损失: 0.1207 | 验证损失: 0.1184
Epoch 015 | 训练损失: 0.1223 | 验证损失: 0.1207
Epoch 016 | 训练损失: 0.1208 | 验证损失: 0.1191
Epoch 017 | 训练损失: 0.1215 | 验证损失: 0.1178
Epoch 018 | 训练损失: 0.1206 | 验证损失: 0.1177
Epoch 019 | 训练损失: 0.1196 | 验证损失: 0.1187
Epoch 020 | 训练损失: 0.1232 | 验证损失: 0.1176
Epoch 021 | 训练损失: 0.1220 | 验证损失: 0.1189
Epoch 022 | 训练损失: 0.1209 | 验证损失: 0.1165
Epoch 023 | 训练损失: 0.1207 | 验证损失: 0.1169
Epoch 024 | 训练损失: 0.1202 | 验证损失: 0.1178
Epoch 025 | 训练损失: 0.1204 | 验证损失: 0.1186


({'mse_conc': 0.30121589452028275,
  'mae_conc': 0.23217247426509857,
  'mse_head': 6.874356746673584,
  'r2_conc': 0.5570262372493744,
  'r2_head': 0.9256022870540619},
 [{'row': array([ 0,  0,  0, ..., 29, 29, 29]),
   'col': array([ 6,  6,  6, ..., 41, 41, 41]),
   'time_step': array([ 0,  1,  2, ..., 37, 38, 39]),
   'pred_conc': array([0.22150159, 0.00793872, 0.01148532, ..., 0.23099153, 0.22659792,
          0.2110572 ], dtype=float32),
   'true_conc': array([6.0698939e-11, 3.9921102e-07, 6.2182323e-07, ..., 1.6965695e-02,
          1.6982598e-02, 1.7324816e-02], dtype=float32),
   'pred_head': array([ 99.75  , 102.4375, 100.25  , ...,  78.625 ,  78.9375,  78.3125],
         dtype=float32),
   'true_head': array([100., 100., 100., ...,  80.,  80.,  80.], dtype=float32)},
  {'row': array([ 0,  0,  0, ..., 29, 29, 29]),
   'col': array([ 6,  6,  6, ..., 41, 41, 41]),
   'time_step': array([ 0,  1,  2, ..., 37, 38, 39]),
   'pred_conc': array([0.22150159, 0.00793872, 0.01148532, ...

In [25]:
import pandas as pd
import torch
import torch.nn.functional as F
import numpy as np
from torch_geometric.data import Data, DataLoader
import os
from torch.cuda.amp import autocast, GradScaler
import matplotlib.pyplot as plt
from torch.optim.lr_scheduler import CosineAnnealingLR
from sklearn.preprocessing import StandardScaler, RobustScaler
from sklearn.metrics import r2_score as sklearn_r2_score

# Training configuration
config = {
    'head_input_dim': 13,
    'conc_input_dim': 15,
    'hidden_dim': 64,
    'num_epochs': 100,
    'lr': 1e-3,
    'weight_decay': 1e-5,
    'patience': 30,
    'save_path': './saved_models'
}

device = torch.device('cuda:1' if torch.cuda.is_available() else 'cpu')
print(f"Selected device: {device}")

def r2_score(y_true, y_pred):
    """
    使用 sklearn.metrics.r2_score 计算 R² 分数，包含 NaN 和 Inf 检查。
    
    参数:
        y_true: 真实值张量
        y_pred: 预测值张量
    
    返回:
        R² 分数，若输入无效则返回 np.nan
    """
    try:
        y_true = y_true.detach().cpu().numpy().flatten()
        y_pred = y_pred.detach().cpu().numpy().flatten()
        
        # 检查输入长度
        if len(y_true) != len(y_pred):
            print(f"Error: y_true and y_pred length mismatch: {len(y_true)} vs {len(y_pred)}")
            return np.nan
        
        # 检查 NaN 或 Inf
        if np.any(np.isnan(y_true)) or np.any(np.isinf(y_true)):
            print("Error: y_true contains NaN or Inf")
            return np.nan
        if np.any(np.isnan(y_pred)) or np.any(np.isinf(y_pred)):
            print("Error: y_pred contains NaN or Inf")
            return np.nan
        
        # 计算 sklearn 的 R² 分数
        r2 = sklearn_r2_score(y_true, y_pred)
        
        # 调试信息：打印 R² 和数据统计
        print(f"R²: {r2:.6f}")
        print(f"y_true mean: {np.mean(y_true):.6f}, variance: {np.var(y_true):.6f}")
        print(f"y_true range: min={np.min(y_true):.6f}, max={np.max(y_true):.6f}")
        print(f"y_pred range: min={np.min(y_pred):.6f}, max={np.max(y_pred):.6f}")
        
        # 检查 R² 异常
        if r2 > 1 or r2 < -1:
            print(f"Warning: Abnormal R² value: {r2}")
            print(f"y_true sample: {y_true[:5]}")
            print(f"y_pred sample: {y_pred[:5]}")
        
        return r2
    
    except Exception as e:
        print(f"Error in r2_score: {e}")
        return np.nan

def train():
    try:
        torch.cuda.empty_cache()
        print("CUDA cache cleared successfully")
    except RuntimeError as e:
        print(f"Failed to clear CUDA cache: {e}")
        return None, None

    grad_scaler = GradScaler()
    head_model = HeadGNN(
        node_features=config['head_input_dim'],
        spatial_dim=config['hidden_dim'],
        temporal_dim=config['hidden_dim']
    ).to(device)
    conc_model = ConcGNN(
        node_features=config['conc_input_dim'],
        spatial_dim=config['hidden_dim'],
        temporal_dim=config['hidden_dim']
    ).to(device)
    criterion_head = PhysicsInformedLoss()
    criterion_conc = ConcLoss()
    optimizer = torch.optim.AdamW(
        list(head_model.parameters()) + list(conc_model.parameters()),
        lr=config['lr'],
        weight_decay=config['weight_decay']
    )
    scheduler = CosineAnnealingLR(optimizer, T_max=config['num_epochs'] * 2, eta_min=1e-5)
    best_val_loss = float('inf')
    early_stop_counter = 0
    accum_steps = 4
    losses = {'train': [], 'val': []}
    val_loss_ema = None
    ema_alpha = 0.9

    for epoch in range(config['num_epochs']):
        head_model.train()
        conc_model.train()
        total_loss = 0
        train_metrics = {
            'mse_conc': 0,
            'mse_head': 0,
            'r2_conc': 0,
            'r2_head': 0
        }
        train_batches = 0

        optimizer.zero_grad()
        for batch_idx, batch in enumerate(train_loader):
            if batch.batch is None or len(batch.batch) == 0 or not hasattr(batch, 'conc_scaler') or not batch.conc_scaler:
                print(f"Skipping invalid batch {batch_idx}")
                continue

            batch = batch.to(device)
            if batch.x.device != device or batch.batch.device != device:
                print(f"Batch {batch_idx} device mismatch: x={batch.x.device}, batch={batch.batch.device}")
                continue

            with torch.amp.autocast("cuda", enabled=True):
                pred_head = head_model(batch)
                
                # 检查预测值是否包含 NaN 或 Inf
                if torch.any(torch.isnan(pred_head)) or torch.any(torch.isinf(pred_head)):
                    print(f"Batch {batch_idx}: pred_head contains NaN or Inf")
                    continue
                if torch.any(torch.isnan(batch.head_y)) or torch.any(torch.isinf(batch.head_y)):
                    print(f"Batch {batch_idx}: head_y contains NaN or Inf")
                    continue

                batch_conc = batch.clone()
                pred_head_2d = pred_head.view(-1, 1) if pred_head.dim() > 2 else pred_head
                batch_conc.x = torch.cat([batch.x, pred_head_2d], dim=1)
                pred_conc = conc_model(batch_conc)

                # 检查浓度预测值是否包含 NaN 或 Inf
                if torch.any(torch.isnan(pred_conc)) or torch.any(torch.isinf(pred_conc)):
                    print(f"Batch {batch_idx}: pred_conc contains NaN or Inf")
                    continue
                if torch.any(torch.isnan(batch.y)) or torch.any(torch.isinf(batch.y)):
                    print(f"Batch {batch_idx}: y contains NaN or Inf")
                    continue

                head_loss, (head_mse, head_flux, head_bc, head_well) = criterion_head(pred_head, batch)
                conc_loss, (conc_mse,) = criterion_conc(pred_conc, batch)
                loss = (0.5 * head_loss + 0.5 * conc_loss) / accum_steps

            grad_scaler.scale(loss).backward()
            if (batch_idx + 1) % accum_steps == 0:
                torch.nn.utils.clip_grad_norm_(list(head_model.parameters()) + list(conc_model.parameters()), max_norm=1.0)
                grad_scaler.step(optimizer)
                grad_scaler.update()
                optimizer.zero_grad()

            total_loss += conc_loss.item()

            max_batch_idx = batch.batch[-1].item() + 1 if batch.batch.numel() > 0 else 0
            for i in range(max_batch_idx):
                mask = batch.batch == i
                if mask.sum() == 0:
                    continue
                mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
                mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()
                r2_conc = r2_score(batch.y[mask], pred_conc[mask])
                r2_head = r2_score(batch.head_y[mask], pred_head[mask])

                train_metrics['mse_conc'] += mse_conc if not np.isinf(mse_conc) else 0
                train_metrics['mse_head'] += mse_head if not np.isinf(mse_head) else 0
                train_metrics['r2_conc'] += r2_conc if not np.isinf(r2_conc) else 0
                train_metrics['r2_head'] += r2_head if not np.isinf(r2_head) else 0

            train_batches += 1

        head_model.eval()
        conc_model.eval()
        val_loss = 0
        val_metrics = {
            'mse_conc': 0,
            'mse_head': 0,
            'r2_conc': 0,
            'r2_head': 0
        }
        val_batches = 0

        with torch.no_grad():
            for batch in val_loader:
                if batch.batch is None or len(batch.batch) == 0 or not hasattr(batch, 'conc_scaler') or not batch.conc_scaler:
                    print(f"Skipping invalid validation batch")
                    continue

                batch = batch.to(device)
                with torch.amp.autocast("cuda", enabled=True):
                    pred_head = head_model(batch)
                    
                    if torch.any(torch.isnan(pred_head)) or torch.any(torch.isinf(pred_head)):
                        print(f"Validation Batch {batch_idx}: pred_head contains NaN or Inf")
                        continue
                    if torch.any(torch.isnan(batch.head_y)) or torch.any(torch.isinf(batch.head_y)):
                        print(f"Validation Batch {batch_idx}: head_y contains NaN or Inf")
                        continue

                    batch_conc = batch.clone()
                    pred_head_2d = pred_head.view(-1, 1) if pred_head.dim() > 2 else pred_head
                    batch_conc.x = torch.cat([batch.x, pred_head_2d], dim=1)
                    pred_conc = conc_model(batch_conc)

                    if torch.any(torch.isnan(pred_conc)) or torch.any(torch.isinf(pred_conc)):
                        print(f"Validation Batch {batch_idx}: pred_conc contains NaN or Inf")
                        continue
                    if torch.any(torch.isnan(batch.y)) or torch.any(torch.isinf(batch.y)):
                        print(f"Validation Batch {batch_idx}: y contains NaN or Inf")
                        continue

                    conc_loss, (conc_mse,) = criterion_conc(pred_conc, batch)

                val_loss += conc_loss.item()

                max_batch_idx = batch.batch[-1].item() + 1 if batch.batch.numel() > 0 else 0
                for i in range(max_batch_idx):
                    mask = batch.batch == i
                    if mask.sum() == 0:
                        continue
                    mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
                    mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()
                    r2_conc = r2_score(batch.y[mask], pred_conc[mask])
                    r2_head = r2_score(batch.head_y[mask], pred_head[mask])

                    val_metrics['mse_conc'] += mse_conc if not np.isinf(mse_conc) else 0
                    val_metrics['mse_head'] += mse_head if not np.isinf(mse_head) else 0
                    val_metrics['r2_conc'] += r2_conc if not np.isinf(r2_conc) else 0
                    val_metrics['r2_head'] += r2_head if not np.isinf(r2_head) else 0

                val_batches += 1

        if train_batches == 0 or val_batches == 0:
            print(f"Epoch {epoch+1}: No valid batches processed (train_batches={train_batches}, val_batches={val_batches})")
            continue

        avg_train_loss = total_loss / train_batches
        avg_val_loss = val_loss / val_batches
        train_metrics = {k: v / train_batches for k, v in train_metrics.items()}
        val_metrics = {k: v / val_batches for k, v in val_metrics.items()}

        print(f"\nEpoch {epoch+1:03d}")
        print("Train Metrics (Standardized):")
        print(f"  Total Loss: {avg_train_loss:.4f}")
        print(f"  Concentration MSE: {train_metrics['mse_conc']:.4f}")
        print(f"  Head MSE: {train_metrics['mse_head']:.4f}")
        print(f"  Concentration R²: {train_metrics['r2_conc']:.4f}")
        print(f"  Head R²: {train_metrics['r2_head']:.4f}")
        print("Validation Metrics (Standardized):")
        print(f"  Total Loss: {avg_val_loss:.4f}")
        print(f"  Concentration MSE: {val_metrics['mse_conc']:.4f}")
        print(f"  Head MSE: {val_metrics['mse_head']:.4f}")
        print(f"  Concentration R²: {val_metrics['r2_conc']:.4f}")
        print(f"  Head R²: {val_metrics['r2_head']:.4f}")

        losses['train'].append(avg_train_loss)
        losses['val'].append(avg_val_loss)

        if val_loss_ema is None:
            val_loss_ema = avg_val_loss
        else:
            val_loss_ema = ema_alpha * val_loss_ema + (1 - ema_alpha) * avg_val_loss

        scheduler.step()
        if val_loss_ema < best_val_loss:
            best_val_loss = val_loss_ema
            early_stop_counter = 0
            os.makedirs(config['save_path'], exist_ok=True)
            torch.save({
                'head_model': head_model.state_dict(),
                'conc_model': conc_model.state_dict(),
            }, os.path.join(config['save_path'], 'best_model.pth'))
        else:
            early_stop_counter += 1

        if torch.cuda.is_available():
            torch.cuda.empty_cache()

        if early_stop_counter >= config['patience']:
            print("Early stopping triggered!")
            break

    mse_records = [{
        'split': split,
        'mse_conc': train_metrics['mse_conc'] if split == 'train' else val_metrics['mse_conc'],
        'mse_head': train_metrics['mse_head'] if split == 'train' else val_metrics['mse_head'],
        'r2_conc': train_metrics['r2_conc'] if split == 'train' else val_metrics['r2_conc'],
        'r2_head': train_metrics['r2_head'] if split == 'train' else val_metrics['r2_head']
    } for split in ['train', 'validation']]
    mse_df = pd.DataFrame(mse_records)
    mse_df.to_csv(os.path.join(config['save_path'], 'global_mse.csv'), index=False)
    print(f"Global MSE saved to {os.path.join(config['save_path'], 'global_mse.csv')}")

    return train_metrics, val_metrics

def evaluate():
    head_model = HeadGNN(
        node_features=config['head_input_dim'],
        spatial_dim=config['hidden_dim'],
        temporal_dim=config['hidden_dim']
    ).to(device)
    conc_model = ConcGNN(
        node_features=config['conc_input_dim'],
        spatial_dim=config['hidden_dim'],
        temporal_dim=config['hidden_dim']
    ).to(device)
    checkpoint = torch.load(os.path.join(config['save_path'], 'best_model.pth'), weights_only=True)
    head_model.load_state_dict(checkpoint['head_model'])
    conc_model.load_state_dict(checkpoint['conc_model'])
    criterion_conc = ConcLoss()
    head_model.eval()
    conc_model.eval()
    test_loss = 0
    metrics = {'mse_conc': 0, 'mae_conc': 0, 'mse_head': 0, 'r2_conc': 0, 'r2_head': 0}
    predictions = []

    if len(test_loader) == 0:
        print("Error: test_loader is empty!")
        return None, None

    with torch.no_grad():
        for batch_idx, batch in enumerate(test_loader):
            batch = batch.to(device)
            with torch.amp.autocast("cuda", enabled=True):
                pred_head = head_model(batch)
                
                if torch.any(torch.isnan(pred_head)) or torch.any(torch.isinf(pred_head)):
                    print(f"Test Batch {batch_idx}: pred_head contains NaN or Inf")
                    continue
                if torch.any(torch.isnan(batch.head_y)) or torch.any(torch.isinf(batch.head_y)):
                    print(f"Test Batch {batch_idx}: head_y contains NaN or Inf")
                    continue

                batch_conc = batch.clone()
                pred_head_2d = pred_head.view(-1, 1) if pred_head.dim() > 2 else pred_head
                batch_conc.x = torch.cat([batch.x, pred_head_2d], dim=1)
                pred_conc = conc_model(batch_conc)

                if torch.any(torch.isnan(pred_conc)) or torch.any(torch.isinf(pred_conc)):
                    print(f"Test Batch {batch_idx}: pred_conc contains NaN or Inf")
                    continue
                if torch.any(torch.isnan(batch.y)) or torch.any(torch.isinf(batch.y)):
                    print(f"Test Batch {batch_idx}: y contains NaN or Inf")
                    continue

                conc_loss, (conc_mse,) = criterion_conc(pred_conc, batch)

            test_loss += conc_loss.item()

            max_batch_idx = batch.batch[-1].item() + 1 if batch.batch.numel() > 0 else 0
            for i in range(max_batch_idx):
                mask = batch.batch == i
                if mask.sum() == 0:
                    continue
                mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
                mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()
                mae_conc = F.l1_loss(pred_conc[mask], batch.y[mask]).item()
                r2_conc = r2_score(batch.y[mask], pred_conc[mask])
                r2_head = r2_score(batch.head_y[mask], pred_head[mask])

                metrics['mse_conc'] += mse_conc if not np.isinf(mse_conc) else 0
                metrics['mae_conc'] += mae_conc if not np.isinf(mae_conc) else 0
                metrics['mse_head'] += mse_head if not np.isinf(mse_head) else 0
                metrics['r2_conc'] += r2_conc if not np.isinf(r2_conc) else 0
                metrics['r2_head'] += r2_head if not np.isinf(r2_head) else 0

                model_names = [batch.model_name[i]] * mask.sum().item()
                predictions.append({
                    'model_name': model_names,
                    'row': batch.row[mask].cpu().numpy(),
                    'col': batch.col[mask].cpu().numpy(),
                    'time_step': batch.time_step[mask].cpu().numpy(),
                    'pred_conc': pred_conc[mask].cpu().numpy().flatten(),
                    'true_conc': batch.y[mask].cpu().numpy().flatten(),
                    'pred_head': pred_head[mask].cpu().numpy().flatten(),
                    'true_head': batch.head_y[mask].cpu().numpy().flatten()
                })

        metrics = {k: v / len(test_loader) for k, v in metrics.items()}

        print(f"Test Metrics (Standardized):")
        print(f"  MSE Conc: {metrics['mse_conc']:.4f}")
        print(f"  MAE Conc: {metrics['mae_conc']:.4f}")
        print(f"  MSE Head: {metrics['mse_head']:.4f}")
        print(f"  Concentration R²: {metrics['r2_conc']:.4f}")
        print(f"  Head R²: {metrics['r2_head']:.4f}")

        mse_records = [{
            'split': 'test',
            'mse_conc': metrics['mse_conc'],
            'mse_head': metrics['mse_head'],
            'mae_conc': metrics['mae_conc'],
            'r2_conc': metrics['r2_conc'],
            'r2_head': metrics['r2_head']
        }]
        mse_df = pd.DataFrame(mse_records)
        mse_df.to_csv(os.path.join(config['save_path'], 'global_mse_test.csv'), index=False)
        print(f"Test global MSE saved to {os.path.join(config['save_path'], 'global_mse_test.csv')}")

        predictions_df = pd.DataFrame()
        for pred in predictions:
            df = pd.DataFrame(pred)
            predictions_df = pd.concat([predictions_df, df], ignore_index=True)
        predictions_df.to_csv(os.path.join(config['save_path'], 'test_predictions.csv'), index=False)
        print(f"Test predictions saved to {os.path.join(config['save_path'], 'test_predictions.csv')}")

    return metrics, predictions

def sensitivity_analysis():
    head_model = HeadGNN(
        node_features=config['head_input_dim'],
        spatial_dim=config['hidden_dim'],
        temporal_dim=config['hidden_dim']
    ).to(device)
    conc_model = ConcGNN(
        node_features=config['conc_input_dim'],
        spatial_dim=config['hidden_dim'],
        temporal_dim=config['hidden_dim']
    ).to(device)
    checkpoint = torch.load(os.path.join(config['save_path'], 'best_model.pth'), weights_only=True)
    head_model.load_state_dict(checkpoint['head_model'])
    conc_model.load_state_dict(checkpoint['conc_model'])
    head_model.eval()
    conc_model.eval()

    baseline_metrics = {'test': {'mse_conc': 0, 'mse_head': 0, 'count': 0}}
    feature_metrics = {f'feature_{i}': {'test': {'mse_conc': 0, 'mse_head': 0, 'count': 0}} for i in range(config['head_input_dim'])}
    edge_metrics = {'test': {'mse_conc': 0, 'mse_head': 0, 'count': 0}}
    node_metrics = {'test': {'mse_conc': 0, 'mse_head': 0, 'count': 0}}

    with torch.no_grad():
        for batch in test_loader:
            batch = batch.to(device)
            with torch.amp.autocast("cuda", enabled=True):
                pred_head = head_model(batch)
                
                if torch.any(torch.isnan(pred_head)) or torch.any(torch.isinf(pred_head)):
                    print(f"Sensitivity Batch: pred_head contains NaN or Inf")
                    continue
                if torch.any(torch.isnan(batch.head_y)) or torch.any(torch.isinf(batch.head_y)):
                    print(f"Sensitivity Batch: head_y contains NaN or Inf")
                    continue

                batch_conc = batch.clone()
                pred_head_2d = pred_head.view(-1, 1) if pred_head.dim() > 2 else pred_head
                batch_conc.x = torch.cat([batch.x, pred_head_2d], dim=1)
                pred_conc = conc_model(batch_conc)

                if torch.any(torch.isnan(pred_conc)) or torch.any(torch.isinf(pred_conc)):
                    print(f"Sensitivity Batch: pred_conc contains NaN or Inf")
                    continue
                if torch.any(torch.isnan(batch.y)) or torch.any(torch.isinf(batch.y)):
                    print(f"Sensitivity Batch: y contains NaN or Inf")
                    continue

                max_batch_idx = batch.batch[-1].item() + 1 if batch.batch.numel() > 0 else 0
                for i in range(max_batch_idx):
                    mask = batch.batch == i
                    if mask.sum() == 0:
                        continue
                    sample_count = mask.sum().item()
                    mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
                    mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()

                    if not np.isinf(mse_conc) and not np.isnan(mse_conc):
                        current = baseline_metrics['test']
                        count = current['count']
                        new_count = count + sample_count
                        current['mse_conc'] = float((current['mse_conc'] * count + mse_conc * sample_count) / new_count)
                        current['mse_head'] = float((current['mse_head'] * count + mse_head * sample_count) / new_count)
                        current['count'] = new_count

            # Node feature sensitivity analysis
            for feature_idx in range(config['head_input_dim']):
                batch_modified = batch.clone()
                batch_modified.x[:, feature_idx] = 0
                with torch.amp.autocast("cuda", enabled=True):
                    pred_head = head_model(batch_modified)
                    
                    if torch.any(torch.isnan(pred_head)) or torch.any(torch.isinf(pred_head)):
                        print(f"Sensitivity Batch, Feature {feature_idx}: pred_head contains NaN or Inf")
                        continue

                    batch_conc = batch.clone()
                    pred_head_2d = pred_head.view(-1, 1) if pred_head.dim() > 2 else pred_head
                    batch_conc.x = torch.cat([batch.x, pred_head_2d], dim=1)
                    pred_conc = conc_model(batch_conc)

                    if torch.any(torch.isnan(pred_conc)) or torch.any(torch.isinf(pred_conc)):
                        print(f"Sensitivity Batch, Feature {feature_idx}: pred_conc contains NaN or Inf")
                        continue

                    for i in range(max_batch_idx):
                        mask = batch.batch == i
                        if mask.sum() == 0:
                            continue
                        sample_count = mask.sum().item()
                        mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
                        mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()

                        if not np.isinf(mse_conc) and not np.isnan(mse_conc):
                            current = feature_metrics[f'feature_{feature_idx}']['test']
                            count = current['count']
                            new_count = count + sample_count
                            current['mse_conc'] = float((current['mse_conc'] * count + mse_conc * sample_count) / new_count)
                            current['mse_head'] = float((current['mse_head'] * count + mse_head * sample_count) / new_count)
                            current['count'] = new_count

            # Edge removal sensitivity analysis
            batch_modified = batch.clone()
            edge_index = batch_modified.edge_index
            num_edges = edge_index.shape[1]
            if num_edges > 0:
                edges_to_remove = torch.randperm(num_edges)[:int(num_edges * 0.1)]
                mask_edges = torch.ones(num_edges, dtype=torch.bool)
                mask_edges[edges_to_remove] = False
                batch_modified.edge_index = edge_index[:, mask_edges]

                with torch.amp.autocast("cuda", enabled=True):
                    pred_head = head_model(batch_modified)
                    
                    if torch.any(torch.isnan(pred_head)) or torch.any(torch.isinf(pred_head)):
                        print(f"Sensitivity Batch, Edge Removal: pred_head contains NaN or Inf")
                        continue

                    batch_conc = batch.clone()
                    pred_head_2d = pred_head.view(-1, 1) if pred_head.dim() > 2 else pred_head
                    batch_conc.x = torch.cat([batch.x, pred_head_2d], dim=1)
                    pred_conc = conc_model(batch_conc)

                    if torch.any(torch.isnan(pred_conc)) or torch.any(torch.isinf(pred_conc)):
                        print(f"Sensitivity Batch, Edge Removal: pred_conc contains NaN or Inf")
                        continue

                    for i in range(max_batch_idx):
                        mask = batch.batch == i
                        if mask.sum() == 0:
                            continue
                        sample_count = mask.sum().item()
                        mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
                        mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()

                        if not np.isinf(mse_conc) and not np.isnan(mse_conc):
                            current = edge_metrics['test']
                            count = current['count']
                            new_count = count + sample_count
                            current['mse_conc'] = float((current['mse_conc'] * count + mse_conc * sample_count) / new_count)
                            current['mse_head'] = float((current['mse_head'] * count + mse_head * sample_count) / new_count)
                            current['count'] = new_count

            # Node removal sensitivity analysis
            batch_modified = batch.clone()
            num_nodes = batch_modified.x.shape[0]
            if num_nodes > 0:
                nodes_to_remove = torch.randperm(num_nodes)[:int(num_nodes * 0.1)]
                mask_nodes = torch.ones(num_nodes, dtype=torch.bool)
                mask_nodes[nodes_to_remove] = False
                batch_modified.x = batch_modified.x[mask_nodes]
                batch_modified.y = batch_modified.y[mask_nodes]
                batch_modified.head_y = batch_modified.head_y[mask_nodes]
                batch_modified.row = batch_modified.row[mask_nodes]
                batch_modified.col = batch_modified.col[mask_nodes]
                batch_modified.time_step = batch_modified.time_step[mask_nodes]
                batch_modified.model_name = batch_modified.model_name[mask_nodes]

                edge_index = batch_modified.edge_index
                edge_mask = mask_nodes[edge_index[0]] & mask_nodes[edge_index[1]]
                batch_modified.edge_index = edge_index[:, edge_mask]

                node_mapping = torch.zeros(num_nodes, dtype=torch.long, device=device)
                node_mapping[mask_nodes] = torch.arange(mask_nodes.sum(), device=device)
                batch_modified.edge_index = node_mapping[batch_modified.edge_index]
                batch_modified.batch = batch_modified.batch[mask_nodes]

                with torch.amp.autocast("cuda", enabled=True):
                    pred_head = head_model(batch_modified)
                    
                    if torch.any(torch.isnan(pred_head)) or torch.any(torch.isinf(pred_head)):
                        print(f"Sensitivity Batch, Node Removal: pred_head contains NaN or Inf")
                        continue

                    batch_conc = batch_modified.clone()
                    pred_head_2d = pred_head.view(-1, 1) if pred_head.dim() > 2 else pred_head
                    batch_conc.x = torch.cat([batch_conc.x, pred_head_2d], dim=1)
                    pred_conc = conc_model(batch_conc)

                    if torch.any(torch.isnan(pred_conc)) or torch.any(torch.isinf(pred_conc)):
                        print(f"Sensitivity Batch, Node Removal: pred_conc contains NaN or Inf")
                        continue

                    for i in range(max_batch_idx):
                        mask = batch_modified.batch == i
                        if mask.sum() == 0:
                            continue
                        sample_count = mask.sum().item()
                        mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask_nodes][batch.batch[mask_nodes] == i]).item()
                        mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask_nodes][batch.batch[mask_nodes] == i]).item()

                        if not np.isinf(mse_conc) and not np.isnan(mse_conc):
                            current = node_metrics['test']
                            count = current['count']
                            new_count = count + sample_count
                            current['mse_conc'] = float((current['mse_conc'] * count + mse_conc * sample_count) / new_count)
                            current['mse_head'] = float((current['mse_head'] * count + mse_head * sample_count) / new_count)
                            current['count'] = new_count

    sensitivity_results = []
    baseline_mse_conc = baseline_metrics['test']['mse_conc']
    baseline_mse_head = baseline_metrics['test']['mse_head']

    for feature_idx in range(config['head_input_dim']):
        mse_conc = feature_metrics[f'feature_{feature_idx}']['test']['mse_conc']
        mse_head = feature_metrics[f'feature_{feature_idx}']['test']['mse_head']
        sensitivity_results.append({
            'type': 'feature',
            'feature': feature_idx,
            'mse_conc_diff': mse_conc - baseline_mse_conc,
            'mse_head_diff': mse_head - baseline_mse_head
        })

    mse_conc = edge_metrics['test']['mse_conc']
    mse_head = edge_metrics['test']['mse_head']
    sensitivity_results.append({
        'type': 'edge',
        'feature': -1,
        'mse_conc_diff': mse_conc - baseline_mse_conc,
        'mse_head_diff': mse_head - baseline_mse_head
    })

    mse_conc = node_metrics['test']['mse_conc']
    mse_head = node_metrics['test']['mse_head']
    sensitivity_results.append({
        'type': 'node',
        'feature': -1,
        'mse_conc_diff': mse_conc - baseline_mse_conc,
        'mse_head_diff': mse_head - baseline_mse_head
    })

    sensitivity_df = pd.DataFrame(sensitivity_results)
    sensitivity_df.to_csv(os.path.join(config['save_path'], 'sensitivity_analysis.csv'), index=False)
    print(f"Sensitivity analysis saved to {os.path.join(config['save_path'], 'sensitivity_analysis.csv')}")

    plt.figure(figsize=(12, 8))
    feature_data = sensitivity_df[sensitivity_df['type'] == 'feature']
    plt.bar(feature_data['feature'], feature_data['mse_conc_diff'], width=0.4, label='Feature Sensitivity')
    plt.xlabel('Feature Index')
    plt.ylabel('MSE Concentration Difference (Standardized)')
    plt.title('Feature Sensitivity Analysis')
    plt.legend()
    plt.savefig(os.path.join(config['save_path'], 'sensitivity_feature_conc.png'))
    plt.close()

    plt.figure(figsize=(12, 8))
    plt.bar(feature_data['feature'], feature_data['mse_head_diff'], width=0.4, label='Feature Sensitivity')
    plt.xlabel('Feature Index')
    plt.ylabel('MSE Head Difference (Standardized)')
    plt.title('Feature Sensitivity Analysis')
    plt.legend()
    plt.savefig(os.path.join(config['save_path'], 'sensitivity_feature_head.png'))
    plt.close()

    return sensitivity_results

Selected device: cuda:1


In [ ]:
train()
evaluate()
sensitivity_analysis()

CUDA cache cleared successfully


/tmp/ipykernel_25255/1076538515.py:85: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  grad_scaler = GradScaler()
/tmp/ipykernel_25255/1076538515.py:176: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
/tmp/ipykernel_25255/1076538515.py:177: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()
/tmp/ipykernel_25255/1076538515.py:176: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])

R²: -0.191997
y_true mean: 0.897516, variance: 4.850609
y_true range: min=-0.118971, max=30.334656
y_pred range: min=-1.245117, max=0.361572
R²: 0.014385
y_true mean: -0.000000, variance: 1.000000
y_true range: min=-2.593300, max=1.937391
y_pred range: min=-0.791016, max=0.469482
R²: -0.069850
y_true mean: 1.004713, variance: 16.773886
y_true range: min=-0.176778, max=110.169167
y_pred range: min=-1.195312, max=0.359863
R²: 0.016127
y_true mean: 0.000000, variance: 1.000000
y_true range: min=-2.589655, max=1.929591
y_pred range: min=-0.791504, max=0.481201
R²: -0.112128
y_true mean: 0.958380, variance: 9.564457
y_true range: min=-0.123088, max=83.298012
y_pred range: min=-1.208008, max=0.322998
R²: 0.015506
y_true mean: 0.000000, variance: 1.000000
y_true range: min=-2.596113, max=1.936203
y_pred range: min=-0.791016, max=0.501953
R²: -0.124012
y_true mean: 0.882964, variance: 7.394965
y_true range: min=-0.173508, max=45.345337
y_pred range: min=-1.226562, max=0.330811
R²: 0.015443
y_t

/tmp/ipykernel_25255/1076538515.py:176: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
/tmp/ipykernel_25255/1076538515.py:177: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()
/tmp/ipykernel_25255/1076538515.py:176: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
/tmp/ipykernel_25255/10765

R²: -0.103065
y_true mean: 1.102392, variance: 13.211525
y_true range: min=-0.136975, max=80.347412
y_pred range: min=-1.238281, max=0.389404
R²: 0.015257
y_true mean: -0.000000, variance: 1.000000
y_true range: min=-2.593029, max=1.940253
y_pred range: min=-0.790039, max=0.484131
R²: -0.115062
y_true mean: 1.049935, variance: 10.931225
y_true range: min=-0.159143, max=44.954601
y_pred range: min=-1.230469, max=0.346680
R²: 0.016060
y_true mean: 0.000000, variance: 1.000000
y_true range: min=-2.590564, max=1.939764
y_pred range: min=-0.790527, max=0.499756
R²: -0.201238
y_true mean: 0.939322, variance: 5.109280
y_true range: min=-0.046471, max=51.039307
y_pred range: min=-1.178711, max=0.400635
R²: 0.014219
y_true mean: 0.000000, variance: 1.000000
y_true range: min=-2.596860, max=1.939407
y_pred range: min=-0.791504, max=0.511719
R²: -0.140307
y_true mean: 0.825431, variance: 5.863214
y_true range: min=-0.194586, max=44.596142
y_pred range: min=-1.200195, max=0.321045
R²: 0.015164
y_t

...

/tmp/ipykernel_25255/1076538515.py:371: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
/tmp/ipykernel_25255/1076538515.py:372: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()
/tmp/ipykernel_25255/1076538515.py:373: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mae_conc = F.l1_loss(pred_conc[mask], batch.y[mask]).item()
/tmp/ipykernel_25255/107653

R²: 0.598162
y_true mean: 0.918381, variance: 8.241614
y_true range: min=-0.171100, max=66.243813
y_pred range: min=-0.281738, max=63.281250
R²: 0.854291
y_true mean: 0.000000, variance: 1.000000
y_true range: min=-2.593485, max=1.938223
y_pred range: min=-3.134766, max=2.308594
R²: 0.579815
y_true mean: 1.102031, variance: 11.556931
y_true range: min=-0.127233, max=64.074326
y_pred range: min=-0.268799, max=58.906250
R²: 0.853109
y_true mean: -0.000000, variance: 1.000000
y_true range: min=-2.591623, max=1.943676
y_pred range: min=-3.134766, max=2.763672
R²: 0.427766
y_true mean: 0.685896, variance: 2.834986
y_true range: min=-0.147573, max=25.516483
y_pred range: min=-0.283691, max=37.218750
R²: 0.854029
y_true mean: 0.000000, variance: 1.000000
y_true range: min=-2.594546, max=1.939013
y_pred range: min=-3.134766, max=1.685547
R²: 0.603055
y_true mean: 1.053789, variance: 8.277164
y_true range: min=-0.065388, max=67.444580
y_pred range: min=-0.282227, max=61.500000
R²: 0.854912
y_tr

/tmp/ipykernel_25255/1076538515.py:371: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
/tmp/ipykernel_25255/1076538515.py:372: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()
/tmp/ipykernel_25255/1076538515.py:373: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mae_conc = F.l1_loss(pred_conc[mask], batch.y[mask]).item()
/tmp/ipykernel_25255/107653

R²: 0.496649
y_true mean: 1.009404, variance: 7.656330
y_true range: min=-0.118099, max=42.858829
y_pred range: min=-0.281250, max=43.531250
R²: 0.854656
y_true mean: -0.000000, variance: 1.000000
y_true range: min=-2.592899, max=1.938657
y_pred range: min=-3.134766, max=2.099609
R²: 0.793291
y_true mean: 1.571146, variance: 82.429733
y_true range: min=-0.032757, max=351.381989
y_pred range: min=-0.274902, max=249.375000
R²: 0.856082
y_true mean: -0.000000, variance: 1.000000
y_true range: min=-2.590131, max=1.950672
y_pred range: min=-3.136719, max=2.958984
R²: 0.597254
y_true mean: 0.849945, variance: 6.625100
y_true range: min=-0.148077, max=43.429283
y_pred range: min=-0.278809, max=48.406250
R²: 0.854718
y_true mean: 0.000000, variance: 1.000000
y_true range: min=-2.592844, max=1.937357
y_pred range: min=-3.134766, max=2.480469
Test Metrics (Standardized):
  MSE Conc: 108.8468
  MAE Conc: 6.1524
  MSE Head: 6.4951
  Concentration R²: 2.1258
  Head R²: 3.2045
Test global MSE saved 

/tmp/ipykernel_25255/1076538515.py:478: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
/tmp/ipykernel_25255/1076538515.py:479: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_head = F.mse_loss(pred_head[mask], batch.head_y[mask]).item()
/tmp/ipykernel_25255/1076538515.py:514: UserWarning: Using a target size (torch.Size([35520])) that is different to the input size (torch.Size([35520, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  mse_conc = F.mse_loss(pred_conc[mask], batch.y[mask]).item()
/tmp/ipykernel_25255/10765

In [1]:
import torch

device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')

In [2]:
device

device(type='cuda', index=0)

In [16]:
export CUDA_LAUNCH_BLOCKING=1
export TORCH_USE_CUDA_DSA=1

SyntaxError: invalid syntax (848178326.py, line 1)